Integer division tutorial
====

Let's divide some integers.

First, a reference implementation of unsigned integer division.
(Everything here is unsigned.  Implementing signed division in terms of unsigned
is left as an exercise to the reader.)

We can use this as a test to verify that our other division algorithm works.

In [28]:
def refdivmod(dividend, divisor):
    quotient = 0
    while dividend >= divisor:
        quotient += 1
        dividend -= divisor
        
    return quotient, dividend

assert refdivmod(20, 5) == (4, 0)
assert refdivmod(23, 5) == (4, 3)

But it's too slow to use in practice:

In [17]:
%%time
refdivmod(10**6, 1)

CPU times: user 128 ms, sys: 0 ns, total: 128 ms
Wall time: 133 ms


(1000000, 0)

So here's a function that validates a candidate implementation of division
against our simple reference implementation above.

In [20]:
def test_divmod(divmod, dividend, divisor):
    result = divmod(dividend, divisor)
    assert result == refdivmod(dividend, divisor), result

test_divmod(refdivmod, 23, 5)

This is pretty much the standard classic long division algorithm
implemented in "constant space".

In [31]:
def iamsmrtdivmod(dividend, divisor):
    # Invariant for both loops: bigdivisor == bigness * divisor
    bigness = 1
    bigdivisor = divisor
    quotient = 0
    
    while bigdivisor <= dividend:
        bigness += bigness                 # to maintain the invariant, when we double the bigness
        bigdivisor += bigdivisor           # we also have to double the bigdivisor

    # Loop invariant: original dividend = current dividend + quotient * divisor
    while bigdivisor >= divisor:
        quotient += bigness
        dividend -= bigdivisor

        if dividend < 0:                   # did we subtract too enthusiastically?
            dividend += bigdivisor         # if so, we can un-subtract
            quotient -= bigness
            bigness >>= 1
            bigdivisor >>= 1
            
    return quotient, dividend

test_divmod(iamsmrtdivmod, 23, 5)

So it seems to work for that case.  Here are another couple of cases:

In [32]:
test_divmod(iamsmrtdivmod, 17, 2)
test_divmod(iamsmrtdivmod, 100, 3)

Those seem to work, though it's probably a good idea to use Hypothesis or something
in order to test the function a little more brutally.

How fast is it on the million-divided-by-one thing that took $\frac 18$ second above?

In [33]:
%%time
iamsmrtdivmod(10**6, 1)

CPU times: user 18 µs, sys: 2 µs, total: 20 µs
Wall time: 23.4 µs


(1000000, 0)

In [35]:
133/.0234  # ms

5683.760683760684

It's about 5700 times faster in that case.  But of course it's asymptotically infinitely faster:

In [26]:
%%time
iamsmrtdivmod(10**9, 3)

CPU times: user 29 µs, sys: 3 µs, total: 32 µs
Wall time: 37 µs


(333333333, 1)